In [ ]:
# default_exp experiment.mining.ir.unsupervised.d2v

# Neural Unsupervised Approaches for SE Traceability [approach d2v]

> Just Paper. Full Experimentation. This module is dedicated to evaluate word2vec/doc2vec or any neural unsupervised approaches on traceability datasets. Consider to Copy the entire notebook for a new and separeted empirical evaluation. 
> Implementing mutual information analysis
> Author: @danaderp April 2020
> Author: @danielrc Nov 2020

In [1]:
from ds4se.mining.ir import Doc2VecSeqVect as d2v
from ds4se.mining.ir import VectorizationType
from ds4se.mining.ir import LinkType
from ds4se.mining.ir import SoftwareArtifacts
from ds4se.mining.ir import Preprocessing
from ds4se.mining.ir import DistanceMetric
from ds4se.mining.ir import LoadLinks
from ds4se.mining.ir import SimilarityMetric

In [2]:
from ds4se.mgmnt.prep.conv import *

In [3]:
from prg import prg

In [4]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

# Artifacts Similarity with BasicSequenceVectorization

We test diferent similarities based on [blog](https://www.kdnuggets.com/2017/08/comparing-distance-measurements-python-scipy.html) and [blog2](https://www.kdnuggets.com/2019/01/comparison-text-distance-metrics.html)

# Experients Set-up

In [5]:
path_data = '../dvc-ds4se/' #dataset path

In [6]:
#Experiment 1.1.3 <<-- doc2vec
path_model_prefix = path_data+'models/bpe/sentencepiece/wiki_py_java_bpe_32k'
path_to_trained_model = path_data+'/models/pv/bpe32k/[doc2vec-Java-py-PVDBOW-500-20E-32k-1595514224.303453].model'
def sacp_params():
        return {
        "vectorizationType": VectorizationType.doc2vec,
        "linkType": LinkType.issue2src,
        "system": 'sacp-python-common',
        "path_to_trained_model": path_to_trained_model,
        "source_type": SoftwareArtifacts.PR.value,
        "target_type": SoftwareArtifacts.PY.value,
        "system_path_config": {
            "system_path": '/tf/data/cisco/sacp_data/[sacp-python-common-all-corpus-1609224778.517111].csv',
            "sep": '~',
            "names": ['ids','bpe32k'],
            "prep": Preprocessing.bpe
        },
        "path_mappings": "/tf/data/cisco/sacp_data/sacp-pr-mappings.csv",
        "saving_path": path_data + 'metrics/traceability/experiments1.1.x/',
        "names": ['Source','Target','Linked?'],
        "model_prefix": path_model_prefix
        }

In [7]:

parameters = sacp_params()
parameters

{'vectorizationType': <VectorizationType.doc2vec: 2>,
 'linkType': <LinkType.issue2src: 3>,
 'system': 'sacp-python-common',
 'path_to_trained_model': '../dvc-ds4se//models/pv/bpe32k/[doc2vec-Java-py-PVDBOW-500-20E-32k-1595514224.303453].model',
 'source_type': 'pr',
 'target_type': 'py',
 'system_path_config': {'system_path': '/tf/data/cisco/sacp_data/[sacp-python-common-all-corpus-1609224778.517111].csv',
  'sep': '~',
  'names': ['ids', 'bpe32k'],
  'prep': <Preprocessing.bpe: 2>},
 'path_mappings': '/tf/data/cisco/sacp_data/sacp-pr-mappings.csv',
 'saving_path': '../dvc-ds4se/metrics/traceability/experiments1.1.x/',
 'names': ['Source', 'Target', 'Linked?'],
 'model_prefix': '../dvc-ds4se/models/bpe/sentencepiece/wiki_py_java_bpe_32k'}

# Artifacts Similarity with Doc2Vec

In [10]:
#[step 1]Creating the Vectorization Class
doc2vec = d2v( params = parameters, logging = logging )

2021-03-11 03:38:31,280 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-03-11 03:38:31,361 : INFO : built Dictionary(3010 unique tokens: ['28', '29', '3', '4)', '7']...) from 362 documents (total 171602 corpus positions)
2021-03-11 03:38:31,611 : INFO : Ignored vocab by BPE{'@', 'γ', '\t', '```', '^', '\r\n\r\n', '\r\n', '\\', '`', '\r\n\r\n@', '\r\n\r\n\r\n'}
2021-03-11 03:38:31,614 : INFO : bpe preprocessing documents, dictionary, and vocab for the test corpus
2021-03-11 03:38:31,617 : INFO : loading Doc2Vec object from ../dvc-ds4se//models/pv/bpe32k/[doc2vec-Java-py-PVDBOW-500-20E-32k-1595514224.303453].model
2021-03-11 03:38:31,857 : INFO : loading vocabulary recursively from ../dvc-ds4se//models/pv/bpe32k/[doc2vec-Java-py-PVDBOW-500-20E-32k-1595514224.303453].model.vocabulary.* with mmap=None
2021-03-11 03:38:31,858 : INFO : loading trainables recursively from ../dvc-ds4se//models/pv/bpe32k/[doc2vec-Java-py-PVDBOW-500-20E-32k-1595514224.303453].model.trainables

In [11]:
doc2vec.df_source.head(2)

ids                                             bpe32k
0  295  ['▁production', '▁merge', '▁*', '▁feed', '▁rel...
1  294  ['▁add', '▁test', '▁fields', '▁for', '▁dare', ...

In [12]:
str(type(doc2vec.new_model))

"<class 'gensim.models.doc2vec.Doc2Vec'>"

In [13]:
#[step1]Apply Doc2Vec Inference
doc2vec.InferDoc2Vec( steps = 200 )

2021-03-11 03:39:46,360 : INFO : Infer Doc2Vec on Source and Target Complete


In [14]:
doc2vec.df_inferred_src.head(2)

ids                                             bpe32k  \
0  295  ['▁production', '▁merge', '▁*', '▁feed', '▁rel...   
1  294  ['▁add', '▁test', '▁fields', '▁for', '▁dare', ...   

                                         inf-doc2vec  
0  [-0.0009429871, 9.838854e-05, 0.0009414563, 0....  
1  [0.0008527204, 0.000113597765, -0.00018898728,...

In [15]:
#[step 2]NonGroundTruth Computation
metric_l = [DistanceMetric.EUC,DistanceMetric.COS,DistanceMetric.MAN, SimilarityMetric.Pearson]
doc2vec.ComputeDistanceArtifacts( sampling=False, samples = 50, metric_list = metric_l )
doc2vec.df_nonground_link.head()

2021-03-11 03:39:46,419 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/auth_utility.py')[[0.018040766939520836, 0.9822789346700174], [0.9985049387905747, 0.0014950612094253302], [0.32699627, 0.7535816226370364], [0.0025339577472802757]]
2021-03-11 03:39:46,425 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/bandit/bandit.py')[[0.019014744088053703, 0.9813400697110908], [1.107482299208641, -0.10748229920864105], [0.35303253, 0.7390805308113142], [0.10766030006545356]]
2021-03-11 03:39:46,428 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/bandit/banditReport.py')[[0.01721368171274662, 0.9830776148392314], [0.921360433101654, 0.07863956689834595], [0.30734006, 0.764911926041624], [0.07549131658354473]]
2021-03-11 03:39:46,434 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/cave/caveCa.py')[[0.018336482346057892, 0.981

2021-03-11 03:39:46,524 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/third_party/corona_lite/corona_lite_func.py')[[0.017936240881681442, 0.9823797992827664], [0.9855495626106858, 0.014450437389314175], [0.3280515, 0.7529828431901664], [0.014636760669328905]]
2021-03-11 03:39:46,528 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/third_party/cve.py')[[0.01744314283132553, 0.9828559040824778], [0.9391479380428791, 0.060852061957120895], [0.31518015, 0.7603521068817325], [0.061237169586527904]]
2021-03-11 03:39:46,531 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/third_party/cve_bd.py')[[0.01831085979938507, 0.9820183987795313], [1.062719278037548, -0.06271927803754807], [0.33385515, 0.7497065917562561], [0.06155786277501967]]
2021-03-11 03:39:46,534 : INFO : Computed distances or similarities ('295', 'sacp-python-common/sacp_python_common/third_party/HubR

2021-03-11 03:39:46,653 : INFO : Computed distances or similarities ('295', 'sacp-python-common/test/python/spotbugs/test_spotbugsdisplay.py')[[0.019001202657818794, 0.9813531106653665], [1.124690055847168, -0.12469005584716797], [0.34510654, 0.7434355336871841], [0.1263637722019482]]
2021-03-11 03:39:46,660 : INFO : Computed distances or similarities ('295', 'sacp-python-common/test/python/test_auth_utility.py')[[0.01789628528058529, 0.9824183607511131], [1.0031392192468047, -0.003139219246804714], [0.326517, 0.7538538975636414], [0.002044889893671289]]
2021-03-11 03:39:46,663 : INFO : Computed distances or similarities ('295', 'sacp-python-common/test/python/third_party/test_binary_scan_func.py')[[0.01840321719646454, 0.9819293410648031], [1.0226282496005297, -0.02262824960052967], [0.3400113, 0.7462623643566518], [0.019406174459752876]]
2021-03-11 03:39:46,666 : INFO : Computed distances or similarities ('295', 'sacp-python-common/test/python/third_party/test_BinaryScan.py')[[0.0178

2021-03-11 03:39:46,750 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/fireException.py')[[0.018220048397779465, 0.9821059814855839], [1.0022517221514136, -0.00225172215141356], [0.3295488, 0.7521348562183194], [0.0027776817386353163]]
2021-03-11 03:39:46,754 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/gosec/gosec_display.py')[[0.017694169655442238, 0.9826134705464286], [0.9982446167850867, 0.0017553832149133086], [0.31903315, 0.7581310622139366], [0.0009013937658287117]]
2021-03-11 03:39:46,757 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/gosec/gosec_report.py')[[0.01825249195098877, 0.9820746896322181], [1.0118182841688395, -0.011818284168839455], [0.33081025, 0.7514219257499712], [0.009163612503616565]]
2021-03-11 03:39:46,761 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/harden_check/harden_func.py')[[0

2021-03-11 03:39:46,856 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/third_party/UploadBom.py')[[0.01823337748646736, 0.9820931253191907], [1.0439562499523163, -0.043956249952316284], [0.33033627, 0.7516896445723594], [0.04113908633331626]]
2021-03-11 03:39:46,870 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/webex_send_func.py')[[0.0176725834608078, 0.9826343130904553], [0.9607648178935051, 0.039235182106494904], [0.3238078, 0.7553966638029921], [0.03795101380466933]]
2021-03-11 03:39:46,878 : INFO : Computed distances or similarities ('294', 'sacp-python-common/sacp_python_common/webexSend.py')[[0.018077140673995018, 0.9822438399294307], [0.980218542739749, 0.019781457260251045], [0.32913172, 0.7523708772494712], [0.01989698104249144]]
2021-03-11 03:39:46,881 : INFO : Computed distances or similarities ('294', 'sacp-python-common/setup.py')[[0.018043944612145424, 0.9822758686325472], [0.9530246

...

2021-03-11 03:41:16,084 : INFO : Computed distances or similarities ('1', 'sacp-python-common/sacp_python_common/webexSend.py')[[0.018002858385443687, 0.9823155129308809], [0.944898284971714, 0.05510171502828598], [0.32802504, 0.7529978483936873], [0.05509980837714865]]
2021-03-11 03:41:16,089 : INFO : Computed distances or similarities ('1', 'sacp-python-common/setup.py')[[0.018950989469885826, 0.981401471056282], [1.0224820729345083, -0.022482072934508324], [0.34740514, 0.7421672766085131], [0.022863103993104157]]
2021-03-11 03:41:16,093 : INFO : Computed distances or similarities ('1', 'sacp-python-common/test/python/bandit/test_bandit.py')[[0.017803719267249107, 0.9825077085785592], [0.9657228216528893, 0.03427717834711075], [0.3264124, 0.7539133325387021], [0.03423016688862194]]
2021-03-11 03:41:16,098 : INFO : Computed distances or similarities ('1', 'sacp-python-common/test/python/cave/test_cave_ca.py')[[0.01793116331100464, 0.982384699518698], [0.9650208465754986, 0.03497915342

2021-03-11 03:41:16,294 : INFO : Computed distances or similarities ('1', 'sacp-python-common/test/python/third_party/unused/test_bd_image.py')[[0.019266407936811447, 0.981097770134689], [1.0701549127697945, -0.07015491276979446], [0.3545623, 0.7382458458144756], [0.07022764429561398]]
2021-03-11 03:41:16,297 : INFO : Computed distances or similarities ('1', 'sacp-python-common/test/python/third_party/unused/test_ipc.py')[[0.01892920210957527, 0.9814224559759555], [1.0643696710467339, -0.06436967104673386], [0.34564573, 0.7431376482540963], [0.06459241103744644]]
2021-03-11 03:41:16,306 : INFO : Computed distances or similarities ('2', 'sacp-python-common/sacp_python_common/auth_utility.py')[[0.018040766939520836, 0.9822789346700174], [0.9985049387905747, 0.0014950612094253302], [0.32699627, 0.7535816226370364], [0.0025339577472802757]]
2021-03-11 03:41:16,309 : INFO : Computed distances or similarities ('2', 'sacp-python-common/sacp_python_common/bandit/bandit.py')[[0.0190147440880537

2021-03-11 03:41:16,418 : INFO : Computed distances or similarities ('2', 'sacp-python-common/sacp_python_common/third_party/bom_bd.py')[[0.017884980887174606, 0.9824292712605049], [0.9969296304043382, 0.0030703695956617594], [0.31961206, 0.7577984722406753], [0.00023329724692106594]]
2021-03-11 03:41:16,422 : INFO : Computed distances or similarities ('2', 'sacp-python-common/sacp_python_common/third_party/corona_lite/corona_lite.py')[[0.01789216324687004, 0.982422339130898], [1.0044820392504334, -0.004482039250433445], [0.32877186, 0.7525746371886269], [0.009778993582772965]]
2021-03-11 03:41:16,425 : INFO : Computed distances or similarities ('2', 'sacp-python-common/sacp_python_common/third_party/corona_lite/corona_lite_func.py')[[0.017936240881681442, 0.9823797992827664], [0.9855495626106858, 0.014450437389314175], [0.3280515, 0.7529828431901664], [0.014636760669328905]]
2021-03-11 03:41:16,427 : INFO : Computed distances or similarities ('2', 'sacp-python-common/sacp_python_commo

2021-03-11 03:41:16,554 : INFO : Computed distances or similarities ('2', 'sacp-python-common/test/python/spotbugs/test_spotbugs.py')[[0.018111996352672577, 0.9822102122187365], [1.0022852714173496, -0.002285271417349577], [0.33199364, 0.7507543357328196], [0.0049057431967580965]]
2021-03-11 03:41:16,557 : INFO : Computed distances or similarities ('2', 'sacp-python-common/test/python/spotbugs/test_spotbugsdisplay.py')[[0.019001202657818794, 0.9813531106653665], [1.124690055847168, -0.12469005584716797], [0.34510654, 0.7434355336871841], [0.1263637722019482]]
2021-03-11 03:41:16,570 : INFO : Computed distances or similarities ('2', 'sacp-python-common/test/python/test_auth_utility.py')[[0.01789628528058529, 0.9824183607511131], [1.0031392192468047, -0.003139219246804714], [0.326517, 0.7538538975636414], [0.002044889893671289]]
2021-03-11 03:41:16,573 : INFO : Computed distances or similarities ('2', 'sacp-python-common/test/python/third_party/test_binary_scan_func.py')[[0.0184032171964

Source                                             Target  \
0    295  sacp-python-common/sacp_python_common/auth_uti...   
1    295  sacp-python-common/sacp_python_common/bandit/b...   
2    295  sacp-python-common/sacp_python_common/bandit/b...   
3    295  sacp-python-common/sacp_python_common/cave/cav...   
4    295  sacp-python-common/sacp_python_common/cave/cav...   

   DistanceMetric.EUC  SimilarityMetric.EUC_sim  DistanceMetric.COS  \
0            0.018041                  0.982279            0.998505   
1            0.019015                  0.981340            1.107482   
2            0.017214                  0.983078            0.921360   
3            0.018336                  0.981994            1.062481   
4            0.017474                  0.982826            0.979056   

   SimilarityMetric.COS_sim  DistanceMetric.MAN  SimilarityMetric.MAN_sim  \
0                  0.001495            0.326996                  0.753582   
1                 -0.107482            0.353033                  0.739081   
2                  0.078640            0.307340                  0.764912   
3                 -0.062481            0.336173                  0.748406   
4                  0.020944            0.314367                  0.760822   

   SimilarityMetric.Pearson  
0                  0.002534  
1                  0.107660  
2                  0.075491  
3                  0.060792  
4                  0.018483

In [16]:
#[step 3]Saving Non-GroundTruth Links
doc2vec.SaveLinks()

2021-03-11 03:41:17,063 : INFO : Saving in...../dvc-ds4se/metrics/traceability/experiments1.1.x/[sacp-python-common-VectorizationType.doc2vec-LinkType.issue2src-False-1615434076.72079].csv


In [17]:
#[step 4]GroundTruthMatching Testing
path_to_ground_truth = parameters['path_mappings']

doc2vec.MatchWithGroundTruth(path_to_ground_truth, semeru_format= True)
doc2vec.df_ground_link

2021-03-11 03:41:17,069 : INFO : generating ground truth
2021-03-11 03:41:17,098 : INFO : processing from semeru_format LibEST
2021-03-11 03:41:17,122 : INFO : Groundtruth links computed


Source                                             Target  \
0        295  sacp-python-common/sacp_python_common/auth_uti...   
1        295  sacp-python-common/sacp_python_common/bandit/b...   
2        295  sacp-python-common/sacp_python_common/bandit/b...   
3        295  sacp-python-common/sacp_python_common/cave/cav...   
4        295  sacp-python-common/sacp_python_common/cave/cav...   
...      ...                                                ...   
21307      2  sacp-python-common/test/python/third_party/tes...   
21308      2  sacp-python-common/test/python/third_party/tes...   
21309      2  sacp-python-common/test/python/third_party/tes...   
21310      2  sacp-python-common/test/python/third_party/unu...   
21311      2  sacp-python-common/test/python/third_party/unu...   

       DistanceMetric.EUC  SimilarityMetric.EUC_sim  DistanceMetric.COS  \
0                0.018041                  0.982279            0.998505   
1                0.019015                  0.981340            1.107482   
2                0.017214                  0.983078            0.921360   
3                0.018336                  0.981994            1.062481   
4                0.017474                  0.982826            0.979056   
...                   ...                       ...                 ...   
21307            0.017721                  0.982587            0.952927   
21308            0.017324                  0.982971            0.936498   
21309            0.017586                  0.982718            0.957133   
21310            0.018841                  0.981507            1.077364   
21311            0.017678                  0.982629            0.978652   

       SimilarityMetric.COS_sim  DistanceMetric.MAN  SimilarityMetric.MAN_sim  \
0                      0.001495            0.326996                  0.753582   
1                     -0.107482            0.353033                  0.739081   
2                      0.078640            0.307340                  0.764912   
3                     -0.062481            0.336173                  0.748406   
4                      0.020944            0.314367                  0.760822   
...                         ...                 ...                       ...   
21307                  0.047073            0.323919                  0.755333   
21308                  0.063502            0.316112                  0.759814   
21309                  0.042867            0.320362                  0.757368   
21310                 -0.077364            0.350694                  0.740360   
21311                  0.021348            0.317747                  0.758871   

       SimilarityMetric.Pearson  Linked?  
0                      0.002534        0  
1                      0.107660        0  
2                      0.075491        0  
3                      0.060792        0  
4                      0.018483        0  
...                         ...      ...  
21307                  0.048615        0  
21308                  0.064016        0  
21309                  0.044887        0  
21310                  0.079344        0  
21311                  0.017428        0  

[21312 rows x 10 columns]

In [23]:
doc2vec.df_ground_link[doc2vec.df_ground_link ['Linked?']==1]

Source                                             Target  \
2        295  sacp-python-common/sacp_python_common/bandit/b...   
7        295  sacp-python-common/sacp_python_common/csbcicd_...   
13       295  sacp-python-common/sacp_python_common/gosec/go...   
17       295  sacp-python-common/sacp_python_common/psb_mapp...   
19       295  sacp-python-common/sacp_python_common/security...   
...      ...                                                ...   
18141     43  sacp-python-common/sacp_python_common/fireExce...   
18215     44  sacp-python-common/sacp_python_common/fireExce...   
18289     42  sacp-python-common/sacp_python_common/fireExce...   
18955     33  sacp-python-common/sacp_python_common/fireExce...   
19103     32  sacp-python-common/sacp_python_common/fireExce...   

       DistanceMetric.EUC  SimilarityMetric.EUC_sim  DistanceMetric.COS  \
2                0.017214                  0.983078            0.921360   
7                0.018172                  0.982153            1.043915   
13               0.018254                  0.982073            1.036214   
17               0.018181                  0.982144            1.045030   
19               0.017654                  0.982652            0.990899   
...                   ...                       ...                 ...   
18141            0.017510                  0.982792            0.937426   
18215            0.018598                  0.981742            1.051497   
18289            0.017617                  0.982688            0.921821   
18955            0.018084                  0.982237            0.988651   
19103            0.018796                  0.981551            1.046079   

       SimilarityMetric.COS_sim  DistanceMetric.MAN  SimilarityMetric.MAN_sim  \
2                      0.078640            0.307340                  0.764912   
7                     -0.043915            0.332554                  0.750438   
13                    -0.036214            0.329878                  0.751949   
17                    -0.045030            0.337923                  0.747427   
19                     0.009101            0.321697                  0.756603   
...                         ...                 ...                       ...   
18141                  0.062574            0.318558                  0.758404   
18215                 -0.051497            0.340763                  0.745844   
18289                  0.078179            0.323830                  0.755384   
18955                  0.011349            0.333195                  0.750078   
19103                 -0.046079            0.346750                  0.742528   

       SimilarityMetric.Pearson  Linked?  
2                      0.075491      1.0  
7                      0.040200      1.0  
13                     0.039093      1.0  
17                     0.043605      1.0  
19                     0.009470      1.0  
...                         ...      ...  
18141                  0.057569      1.0  
18215                  0.048234      1.0  
18289                  0.080816      1.0  
18955                  0.011835      1.0  
19103                  0.043452      1.0  

[547 rows x 10 columns]

In [19]:
#[step 4.1]GroundTruthMatching Testing For CISCO Mappings <--- Only SACP
doc2vec.MatchWithGroundTruth(from_mappings=True)
doc2vec.df_ground_link

2021-03-11 03:41:17,182 : INFO : ground truth from mappings
2021-03-11 03:41:17,183 : INFO : processing from mappings SACP
2021-03-11 03:41:17,194 : INFO : processing from mappings SACP
2021-03-11 03:41:17,204 : INFO : processing from mappings SACP
2021-03-11 03:41:17,214 : INFO : processing from mappings SACP
2021-03-11 03:41:17,224 : INFO : processing from mappings SACP
2021-03-11 03:41:17,234 : INFO : processing from mappings SACP
2021-03-11 03:41:17,245 : INFO : processing from mappings SACP
2021-03-11 03:41:17,255 : INFO : processing from mappings SACP
2021-03-11 03:41:17,266 : INFO : processing from mappings SACP
2021-03-11 03:41:17,277 : INFO : processing from mappings SACP
2021-03-11 03:41:17,287 : INFO : processing from mappings SACP
2021-03-11 03:41:17,295 : INFO : processing from mappings SACP
2021-03-11 03:41:17,308 : INFO : processing from mappings SACP
2021-03-11 03:41:17,319 : INFO : processing from mappings SACP
2021-03-11 03:41:17,329 : INFO : processing from mappings 

2021-03-11 03:41:18,613 : INFO : processing from mappings SACP
2021-03-11 03:41:18,625 : INFO : processing from mappings SACP
2021-03-11 03:41:18,642 : INFO : processing from mappings SACP
2021-03-11 03:41:18,652 : INFO : processing from mappings SACP
2021-03-11 03:41:18,667 : INFO : processing from mappings SACP
2021-03-11 03:41:18,676 : INFO : processing from mappings SACP
2021-03-11 03:41:18,693 : INFO : processing from mappings SACP
2021-03-11 03:41:18,705 : INFO : processing from mappings SACP
2021-03-11 03:41:18,713 : INFO : processing from mappings SACP
2021-03-11 03:41:18,723 : INFO : processing from mappings SACP
2021-03-11 03:41:18,731 : INFO : processing from mappings SACP
2021-03-11 03:41:18,740 : INFO : processing from mappings SACP
2021-03-11 03:41:18,750 : INFO : processing from mappings SACP
2021-03-11 03:41:18,759 : INFO : processing from mappings SACP
2021-03-11 03:41:18,769 : INFO : processing from mappings SACP
2021-03-11 03:41:18,779 : INFO : processing from mappin

2021-03-11 03:41:20,026 : INFO : processing from mappings SACP
2021-03-11 03:41:20,035 : INFO : processing from mappings SACP
2021-03-11 03:41:20,047 : INFO : processing from mappings SACP
2021-03-11 03:41:20,057 : INFO : processing from mappings SACP
2021-03-11 03:41:20,066 : INFO : processing from mappings SACP
2021-03-11 03:41:20,076 : INFO : processing from mappings SACP
2021-03-11 03:41:20,088 : INFO : processing from mappings SACP
2021-03-11 03:41:20,097 : INFO : processing from mappings SACP
2021-03-11 03:41:20,108 : INFO : processing from mappings SACP
2021-03-11 03:41:20,119 : INFO : processing from mappings SACP
2021-03-11 03:41:20,127 : INFO : processing from mappings SACP
2021-03-11 03:41:20,138 : INFO : processing from mappings SACP
2021-03-11 03:41:20,147 : INFO : processing from mappings SACP
2021-03-11 03:41:20,156 : INFO : processing from mappings SACP
2021-03-11 03:41:20,166 : INFO : processing from mappings SACP
2021-03-11 03:41:20,176 : INFO : processing from mappin

2021-03-11 03:41:21,375 : INFO : processing from mappings SACP
2021-03-11 03:41:21,384 : INFO : processing from mappings SACP
2021-03-11 03:41:21,393 : INFO : processing from mappings SACP
2021-03-11 03:41:21,402 : INFO : processing from mappings SACP
2021-03-11 03:41:21,411 : INFO : processing from mappings SACP
2021-03-11 03:41:21,420 : INFO : processing from mappings SACP
2021-03-11 03:41:21,429 : INFO : processing from mappings SACP
2021-03-11 03:41:21,439 : INFO : processing from mappings SACP
2021-03-11 03:41:21,451 : INFO : processing from mappings SACP
2021-03-11 03:41:21,462 : INFO : processing from mappings SACP
2021-03-11 03:41:21,473 : INFO : processing from mappings SACP
2021-03-11 03:41:21,484 : INFO : processing from mappings SACP
2021-03-11 03:41:21,495 : INFO : processing from mappings SACP
2021-03-11 03:41:21,504 : INFO : processing from mappings SACP
2021-03-11 03:41:21,516 : INFO : processing from mappings SACP
2021-03-11 03:41:21,526 : INFO : processing from mappin

2021-03-11 03:41:22,693 : INFO : processing from mappings SACP
2021-03-11 03:41:22,702 : INFO : processing from mappings SACP
2021-03-11 03:41:22,711 : INFO : processing from mappings SACP
2021-03-11 03:41:22,720 : INFO : processing from mappings SACP
2021-03-11 03:41:22,730 : INFO : processing from mappings SACP
2021-03-11 03:41:22,739 : INFO : processing from mappings SACP
2021-03-11 03:41:22,748 : INFO : processing from mappings SACP
2021-03-11 03:41:22,758 : INFO : processing from mappings SACP
2021-03-11 03:41:22,767 : INFO : processing from mappings SACP
2021-03-11 03:41:22,776 : INFO : processing from mappings SACP
2021-03-11 03:41:22,786 : INFO : processing from mappings SACP
2021-03-11 03:41:22,795 : INFO : processing from mappings SACP
2021-03-11 03:41:22,804 : INFO : processing from mappings SACP
2021-03-11 03:41:22,822 : INFO : processing from mappings SACP
2021-03-11 03:41:22,831 : INFO : processing from mappings SACP
2021-03-11 03:41:22,840 : INFO : processing from mappin

...

2021-03-11 03:41:40,230 : INFO : processing from mappings SACP
2021-03-11 03:41:40,246 : INFO : processing from mappings SACP
2021-03-11 03:41:40,255 : INFO : processing from mappings SACP
2021-03-11 03:41:40,263 : INFO : processing from mappings SACP
2021-03-11 03:41:40,272 : INFO : processing from mappings SACP
2021-03-11 03:41:40,281 : INFO : processing from mappings SACP
2021-03-11 03:41:40,292 : INFO : processing from mappings SACP
2021-03-11 03:41:40,303 : INFO : processing from mappings SACP
2021-03-11 03:41:40,312 : INFO : processing from mappings SACP
2021-03-11 03:41:40,320 : INFO : processing from mappings SACP
2021-03-11 03:41:40,328 : INFO : processing from mappings SACP
2021-03-11 03:41:40,338 : INFO : processing from mappings SACP
2021-03-11 03:41:40,347 : INFO : processing from mappings SACP
2021-03-11 03:41:40,355 : INFO : processing from mappings SACP
2021-03-11 03:41:40,365 : INFO : processing from mappings SACP
2021-03-11 03:41:40,373 : INFO : processing from mappin

2021-03-11 03:41:41,573 : INFO : processing from mappings SACP
2021-03-11 03:41:41,581 : INFO : processing from mappings SACP
2021-03-11 03:41:41,593 : INFO : processing from mappings SACP
2021-03-11 03:41:41,602 : INFO : processing from mappings SACP
2021-03-11 03:41:41,613 : INFO : processing from mappings SACP
2021-03-11 03:41:41,622 : INFO : processing from mappings SACP
2021-03-11 03:41:41,631 : INFO : processing from mappings SACP
2021-03-11 03:41:41,640 : INFO : processing from mappings SACP
2021-03-11 03:41:41,649 : INFO : processing from mappings SACP
2021-03-11 03:41:41,663 : INFO : processing from mappings SACP
2021-03-11 03:41:41,673 : INFO : processing from mappings SACP
2021-03-11 03:41:41,682 : INFO : processing from mappings SACP
2021-03-11 03:41:41,691 : INFO : processing from mappings SACP
2021-03-11 03:41:41,701 : INFO : processing from mappings SACP
2021-03-11 03:41:41,710 : INFO : processing from mappings SACP
2021-03-11 03:41:41,721 : INFO : processing from mappin

2021-03-11 03:41:42,910 : INFO : processing from mappings SACP
2021-03-11 03:41:42,919 : INFO : processing from mappings SACP
2021-03-11 03:41:42,929 : INFO : processing from mappings SACP
2021-03-11 03:41:42,939 : INFO : processing from mappings SACP
2021-03-11 03:41:42,956 : INFO : processing from mappings SACP
2021-03-11 03:41:42,970 : INFO : processing from mappings SACP
2021-03-11 03:41:42,985 : INFO : processing from mappings SACP
2021-03-11 03:41:42,992 : INFO : processing from mappings SACP
2021-03-11 03:41:43,004 : INFO : processing from mappings SACP
2021-03-11 03:41:43,012 : INFO : processing from mappings SACP
2021-03-11 03:41:43,020 : INFO : processing from mappings SACP
2021-03-11 03:41:43,030 : INFO : processing from mappings SACP
2021-03-11 03:41:43,041 : INFO : processing from mappings SACP
2021-03-11 03:41:43,051 : INFO : processing from mappings SACP
2021-03-11 03:41:43,063 : INFO : processing from mappings SACP
2021-03-11 03:41:43,072 : INFO : processing from mappin

2021-03-11 03:41:44,245 : INFO : processing from mappings SACP
2021-03-11 03:41:44,254 : INFO : processing from mappings SACP
2021-03-11 03:41:44,263 : INFO : processing from mappings SACP
2021-03-11 03:41:44,274 : INFO : processing from mappings SACP
2021-03-11 03:41:44,282 : INFO : processing from mappings SACP
2021-03-11 03:41:44,291 : INFO : processing from mappings SACP
2021-03-11 03:41:44,300 : INFO : processing from mappings SACP
2021-03-11 03:41:44,308 : INFO : processing from mappings SACP
2021-03-11 03:41:44,318 : INFO : processing from mappings SACP
2021-03-11 03:41:44,327 : INFO : processing from mappings SACP
2021-03-11 03:41:44,336 : INFO : processing from mappings SACP
2021-03-11 03:41:44,345 : INFO : processing from mappings SACP
2021-03-11 03:41:44,353 : INFO : processing from mappings SACP
2021-03-11 03:41:44,362 : INFO : processing from mappings SACP
2021-03-11 03:41:44,371 : INFO : processing from mappings SACP
2021-03-11 03:41:44,381 : INFO : processing from mappin

Source                                             Target  \
0        295  sacp-python-common/sacp_python_common/auth_uti...   
1        295  sacp-python-common/sacp_python_common/bandit/b...   
2        295  sacp-python-common/sacp_python_common/bandit/b...   
3        295  sacp-python-common/sacp_python_common/cave/cav...   
4        295  sacp-python-common/sacp_python_common/cave/cav...   
...      ...                                                ...   
21307      2  sacp-python-common/test/python/third_party/tes...   
21308      2  sacp-python-common/test/python/third_party/tes...   
21309      2  sacp-python-common/test/python/third_party/tes...   
21310      2  sacp-python-common/test/python/third_party/unu...   
21311      2  sacp-python-common/test/python/third_party/unu...   

       DistanceMetric.EUC  SimilarityMetric.EUC_sim  DistanceMetric.COS  \
0                0.018041                  0.982279            0.998505   
1                0.019015                  0.981340            1.107482   
2                0.017214                  0.983078            0.921360   
3                0.018336                  0.981994            1.062481   
4                0.017474                  0.982826            0.979056   
...                   ...                       ...                 ...   
21307            0.017721                  0.982587            0.952927   
21308            0.017324                  0.982971            0.936498   
21309            0.017586                  0.982718            0.957133   
21310            0.018841                  0.981507            1.077364   
21311            0.017678                  0.982629            0.978652   

       SimilarityMetric.COS_sim  DistanceMetric.MAN  SimilarityMetric.MAN_sim  \
0                      0.001495            0.326996                  0.753582   
1                     -0.107482            0.353033                  0.739081   
2                      0.078640            0.307340                  0.764912   
3                     -0.062481            0.336173                  0.748406   
4                      0.020944            0.314367                  0.760822   
...                         ...                 ...                       ...   
21307                  0.047073            0.323919                  0.755333   
21308                  0.063502            0.316112                  0.759814   
21309                  0.042867            0.320362                  0.757368   
21310                 -0.077364            0.350694                  0.740360   
21311                  0.021348            0.317747                  0.758871   

       SimilarityMetric.Pearson  Linked?  
0                      0.002534      0.0  
1                      0.107660      0.0  
2                      0.075491      1.0  
3                      0.060792      0.0  
4                      0.018483      0.0  
...                         ...      ...  
21307                  0.048615      0.0  
21308                  0.064016      0.0  
21309                  0.044887      0.0  
21310                  0.079344      0.0  
21311                  0.017428      0.0  

[21312 rows x 10 columns]

In [20]:
#[step 5]Saving GroundTruth Links
doc2vec.SaveLinks(grtruth = True)

2021-03-11 03:41:45,143 : INFO : Saving in...../dvc-ds4se/metrics/traceability/experiments1.1.x/[sacp-python-common-VectorizationType.doc2vec-LinkType.issue2src-True-1615434104.842028].csv


In [22]:
#Loading Non-GroundTruth Links (change the timestamp with the assigned in the previous step)
df_glinks = LoadLinks(timestamp=1615434104.842028, params=parameters,grtruth = True, logging = logging)
df_glinks.head()

2021-03-11 03:43:10,174 : INFO : Loading computed links from... ../dvc-ds4se/metrics/traceability/experiments1.1.x/[sacp-python-common-VectorizationType.doc2vec-LinkType.issue2src-True-1615434104.842028].csv
2021-03-11 03:43:10,245 : INFO : df_x.dtypesSource                       object
Target                       object
DistanceMetric.EUC          float64
SimilarityMetric.EUC_sim    float64
DistanceMetric.COS          float64
SimilarityMetric.COS_sim    float64
DistanceMetric.MAN          float64
SimilarityMetric.MAN_sim    float64
SimilarityMetric.Pearson    float64
Linked?                     float64
dtype: object


Source                                             Target  \
0    295  sacp-python-common/sacp_python_common/auth_uti...   
1    295  sacp-python-common/sacp_python_common/bandit/b...   
2    295  sacp-python-common/sacp_python_common/bandit/b...   
3    295  sacp-python-common/sacp_python_common/cave/cav...   
4    295  sacp-python-common/sacp_python_common/cave/cav...   

   DistanceMetric.EUC  SimilarityMetric.EUC_sim  DistanceMetric.COS  \
0            0.018041                  0.982279            0.998505   
1            0.019015                  0.981340            1.107482   
2            0.017214                  0.983078            0.921360   
3            0.018336                  0.981994            1.062481   
4            0.017474                  0.982826            0.979056   

   SimilarityMetric.COS_sim  DistanceMetric.MAN  SimilarityMetric.MAN_sim  \
0                  0.001495            0.326996                  0.753582   
1                 -0.107482            0.353033                  0.739081   
2                  0.078640            0.307340                  0.764912   
3                 -0.062481            0.336173                  0.748406   
4                  0.020944            0.314367                  0.760822   

   SimilarityMetric.Pearson  Linked?  
0                  0.002534      0.0  
1                  0.107660      0.0  
2                  0.075491      1.0  
3                  0.060792      0.0  
4                  0.018483      0.0